In [2]:
from transformers import (
    RobertaTokenizerFast,
    RobertaForSequenceClassification,
    TrainingArguments,
    Trainer,
    AutoConfig,
)
from sklearn.model_selection import train_test_split
import pandas as pd


In [3]:
import os
folder_path = 'formatted_data/'

# Get the list of all files in the folder
file_names = os.listdir(folder_path)
max_file_name=max([int(i.split("_")[-1][:-4]) for i in file_names])

In [4]:
device="cuda"
df=pd.read_csv("formatted_data\data_"+str(max_file_name)+".csv")

<>:2: SyntaxWarning: invalid escape sequence '\d'
<>:2: SyntaxWarning: invalid escape sequence '\d'
C:\Users\rajst\AppData\Local\Temp\ipykernel_18180\3256903659.py:2: SyntaxWarning: invalid escape sequence '\d'
  df=pd.read_csv("formatted_data\data_"+str(max_file_name)+".csv")


In [5]:
from sklearn.model_selection import train_test_split
from transformers import AutoTokenizer, AutoModelForSequenceClassification
import torch
import pandas as pd

# Assuming df is already defined and contains 'text' and 'label' columns
# Convert labels to numerical format if they are not already (e.g., if they are strings)
label_mapping = {label: idx for idx, label in enumerate(df['label'].unique())}
df['label'] = df['label'].map(label_mapping)

# Split the dataset into training and testing sets
X_train, X_test, y_train, y_test = train_test_split(df['prompt'], df['label'], test_size=0.1, random_state=42)

# Define the local directory to save the model
local_model_dir = "allenai/longformer-base-4096"

# Load the tokenizer and model from the local directory
tokenizer = AutoTokenizer.from_pretrained(local_model_dir, add_prefix_space=True)
num_labels = len(df['label'].unique())
model = AutoModelForSequenceClassification.from_pretrained(local_model_dir, num_labels=num_labels)

# Tokenize the data
train_encodings = tokenizer(X_train.tolist(), truncation=True, padding=True, max_length=128)
test_encodings = tokenizer(X_test.tolist(), truncation=True, padding=True, max_length=128)

# Create a Dataset class
class CustomDataset(torch.utils.data.Dataset):
    def __init__(self, encodings, labels):
        self.encodings = encodings
        self.labels = labels

    def __getitem__(self, idx):
        # Convert the encodings into tensors
        item = {key: torch.tensor(val[idx]) for key, val in self.encodings.items()}
        # Add the labels as a tensor
        item['labels'] = torch.tensor(self.labels[idx])
        return item

    def __len__(self):
        return len(self.labels)

# Create dataset objects
train_dataset = CustomDataset(train_encodings, y_train.tolist())
test_dataset = CustomDataset(test_encodings, y_test.tolist())

# Check the structure of the first item for verification
# print(train_dataset[0])


d:\external\Experiments\image_designing\env\Lib\site-packages\transformers\tokenization_utils_base.py:1601: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be depracted in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(
Some weights of LongformerForSequenceClassification were not initialized from the model checkpoint at allenai/longformer-base-4096 and are newly initialized: ['classifier.dense.bias', 'classifier.dense.weight', 'classifier.out_proj.bias', 'classifier.out_proj.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [6]:
training_args = TrainingArguments(
output_dir="results/",
num_train_epochs=1,
per_device_train_batch_size=12,
per_device_eval_batch_size=12,
warmup_steps=500,
weight_decay=0.0001,
logging_dir='./logs',
logging_steps=10,
evaluation_strategy="epoch",


)


trainer = Trainer(
model=model.to(device),
args=training_args,
train_dataset=train_dataset,
eval_dataset=test_dataset,
compute_metrics=lambda p: {'accuracy': (p.predictions. argmax(-1) == p.label_ids).astype(float).mean().item()})



trainer.train()

# trainer.evaluate()

d:\external\Experiments\image_designing\env\Lib\site-packages\transformers\training_args.py:1525: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(
  0%|          | 0/3003 [00:00<?, ?it/s]Initializing global attention on CLS token...
Input ids are automatically padded to be a multiple of `config.attention_window`: 512
  0%|          | 10/3003 [00:30<1:46:54,  2.14s/it]

{'loss': 0.7056, 'grad_norm': 2.5160858631134033, 'learning_rate': 1.0000000000000002e-06, 'epoch': 0.0}


  1%|          | 20/3003 [00:50<1:40:31,  2.02s/it]

{'loss': 0.6966, 'grad_norm': 1.4280675649642944, 'learning_rate': 2.0000000000000003e-06, 'epoch': 0.01}


  1%|          | 30/3003 [01:10<1:39:47,  2.01s/it]

...

100%|█████████▉| 3000/3003 [1:47:21<00:05,  1.99s/it]

{'loss': 0.0001, 'grad_norm': 0.0014699451858177781, 'learning_rate': 5.992808629644426e-08, 'epoch': 1.0}


                                                     
100%|██████████| 3003/3003 [1:52:09<00:00,  2.24s/it]

{'eval_loss': 0.0015117675065994263, 'eval_accuracy': 0.9997502497502497, 'eval_runtime': 168.0335, 'eval_samples_per_second': 23.829, 'eval_steps_per_second': 1.988, 'epoch': 1.0}
{'train_runtime': 6729.8702, 'train_samples_per_second': 5.355, 'train_steps_per_second': 0.446, 'train_loss': 0.02579331953068177, 'epoch': 1.0}


TrainOutput(global_step=3003, training_loss=0.02579331953068177, metrics={'train_runtime': 6729.8702, 'train_samples_per_second': 5.355, 'train_steps_per_second': 0.446, 'total_flos': 2958788084668416.0, 'train_loss': 0.02579331953068177, 'epoch': 1.0})

In [7]:
import os
folder_path = 'model_collection/'

# Get the list of all files in the folder
file_names = os.listdir(folder_path)
max_file_name=max([int(i.split("_")[-1]) for i in file_names]+[1])

In [8]:
max_file_name

3

In [9]:
model.save_pretrained("model_collection/model_"+str(max_file_name+1))
tokenizer.save_pretrained("model_collection/model_"+str(max_file_name+1))

('model_collection/model_4\\tokenizer_config.json',
 'model_collection/model_4\\special_tokens_map.json',
 'model_collection/model_4\\vocab.json',
 'model_collection/model_4\\merges.txt',
 'model_collection/model_4\\added_tokens.json',
 'model_collection/model_4\\tokenizer.json')

In [10]:
"model_collection/model_"+str(max_file_name)+"/"

'model_collection/model_3/'

In [11]:
from transformers import pipeline

classifier = pipeline("text-classification", model = "model_collection/model_"+str(max_file_name+1)+"/")
# classifier("create a painting a painting")

Hardware accelerator e.g. GPU is available in the environment, but no `device` argument is passed to the `Pipeline` object. Model will be on CPU.


In [12]:
classifier("generate something new")

[{'label': 'LABEL_1', 'score': 0.9998732805252075}]

In [1]:
from transformers import pipeline

classifier = pipeline("text-classification", model = "model_collection/model_"+str(3)+"/")
# classifier("create a painting a painting")

d:\external\Experiments\image_designing\env\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
Hardware accelerator e.g. GPU is available in the environment, but no `device` argument is passed to the `Pipeline` object. Model will be on CPU.


In [11]:
print(classifier("show me photo of a forest"))

[{'label': 'LABEL_0', 'score': 0.9999868869781494}]
